# Train/Validation/Test Split Notebook - Train Data Split  

Objective: Split the full dataset into training data.  

##### Train data (this notebook):  
3 month data = January and February of 2015    
full data = 2015 through 2017    
Steps:   
A) Drop rows:  
- Where weather readings are suspect or erroneous   
- Where report_types are SY-MT, FM-16, SOD,SOM  
- Where there are nulls  
- Where there are 99999 (missing) data    

B) Bin Data    
C) Use train data to create Airport PageRank helper Table     
D) Join Airport PageRank to final table    
E) Create helper table of averages  grouped by day_of_week and origin for imputing validation data     
F) Create helper table of averages  for imputing validation data (when ORIGIN not in training data)     


 ##### Validation/Test Data (other notebook): 
3 month data = March 2015 (validation)  
full data = 2018 (validation), 2019 (test)    
Steps:  
A) Join PageRank helper table created previously to test data  
B) Imputations  
- Join imputed value table (averages at each ORIGIN) with full data (joins columns with feature averages to full data)  
- For averages with null values, impute with second helper table of averages of all training data (null averages are caused by ORIGIN in validation/test data that are not in train data)   
- Finally, impute the suspect or erroneous, nulls, and 99999 (missing) data in the full table with these averages  

C) Bin Data

In [0]:
#Import packages
from pyspark.sql import functions as f
from pyspark.sql.types import StructType, StructField, StringType, DoubleType, IntegerType, NullType, ShortType, DateType, BooleanType, BinaryType, FloatType
from pyspark.sql import SQLContext
from pyspark.sql.functions import isnan, when, count, col, udf, date_trunc, max as max_, sum as sum_, avg as avg_, min as min_
from pyspark.ml.feature import Bucketizer
from pyspark.sql.types import TimestampType
from pyspark.sql.functions import udf, date_trunc, col
from datetime import datetime, timedelta
from pyspark.sql.types import TimestampType
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from datetime import datetime
from pytz import timezone
import pytz

sqlContext = SQLContext(sc)

## Get Joined Data from Shared Folder

In [0]:
#READING PARQUET File from Shared Directory
filename = "flight_weather_data_3m"              # 3 Month Data
joined_data_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/join_data_folder/"+filename+"/part-00*.parquet")

filename = "flight_weather_data"               # Full data
joined_data = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/join_data_folder/"+filename+"/part-00*.parquet")

joined_data_3m.display()
print("joined_data_3m Shape:", joined_data_3m.count(), len(joined_data_3m.columns))
joined_data.display()
print("joined_data Shape:", joined_data.count(), len(joined_data.columns))

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY DELAY LATITUDE LONGITUDE ELEVATION REPORT_TYPE WND_SPEED WND_SPEED_QUAL CIG_HEIGHT CIG_QUAL VIS_DIST VIS_DIST_QUAL VIS_VAR VIS_VAR_QUAL TEMP TEMP_QUAL DEW_TEMP DEW_TEMP_QUAL SLPRESS SLPRESS_QUAL DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_REPORT_TYPE DEST_WND_SPEED DEST_WND_SPEED_QUAL DEST_CIG_HEIGHT DEST_CIG_QUAL DEST_VIS_DIST DEST_VIS_DIST_QUAL DEST_VIS_VAR DEST_VIS_VAR_QUAL DEST_TEMP DEST_TEMP_QUAL DEST_DEW_TEMP DEST_DEW_TEMP_QUAL DEST_SLPRESS DEST_SLPRESS_QUAL FLIGHTS_PER_DAY 2015 1 4 AA DFW TX CLE OH 1415 155.0 1021.0 0 0 0 32.8978 -97.0189 170.7 FM-16 31 5 122 5 3219 5 N 5 6 5 0 5 99999 9 41.4057 -81.852 238.0 FM-15 88 5 22000 5 16093 5 N 5 -11 5 -128 5 10169 5 13951 2015 1 4 AA DFW TX DTW MI 1030 150.0 986.0 0 0 1 32.8978 -97.0189 170.7 FM-16 21 5 396 5 3219 5 N 5 -6 5 -17 5 99999 9 42.2313 -83.3308 192.3 FM-15 88 5 7315 5 16093 5 N 5 -72 5 -133 5 10171 5 13951 2015 1 4 AA DFW TX IND IN 1625 120.0 761.0 0 0 1 32.8978 -97.0189 170.7 FM-16 26 5 183 5 2414 5 N 5 17 5 6 5 99999 9 39.72517 -86.28168 241.1 FM-15 88 5 7620 5 16093 5 N 5 11 5 -94 5 10190 5 13951 2015 1 4 AA PHX AZ DFW TX 200 120.0 868.0 0 0 1 33.4277 -112.0038 337.4 SOM 9999 9 99999 9 999999 9 9 9 9999 9 9999 9 99999 9 32.8978 -97.0189 170.7 FM-15 26 5 1372 5 16093 5 N 5 11 5 -50 5 10296 5 13951 2015 1 4 AA PHX AZ DFW TX 200 120.0 868.0 0 0 1 33.4277 -112.0038 337.4 SOD 9999 9 99999 9 999999 9 9 9 9999 9 9999 9 99999 9 32.8978 -97.0189 170.7 FM-15 26 5 1372 5 16093 5 N 5 11 5 -50 5 10296 5 13951 2015 1 4 AS ATL GA SEA WA 1810 334.0 2182.0 0 0 1 33.6301 -84.4418 307.8 FM-15 15 5 1981 5 16093 5 N 5 133 5 -28 5 10250 5 47.4444 -122.3138 112.8 FM-15 21 5 22000 5 16093 5 N 5 44 5 -44 5 10263 5 13951 2015 1 4 AS OGG HI BLI WA 1425 353.0 2681.0 0 0 1 20.89972 -156.42861 15.5 FM-15 41 5 22000 5 16093 5 N 5 239 5 139 5 10122 5 48.79389 -122.53722 45.4 FM-15 15 5 22000 5 16093 5 N 5 39 5 -33 5 10263 5 13951 2015 1 4 AS SAT TX SEA WA 1830 270.0 1774.0 0 0 0 29.5443 -98.4839 240.5 FM-15 21 5 213 5 16093 5 N 5 50 5 33 5 10191 5 47.4444 -122.3138 112.8 FM-15 21 5 22000 5 16093 5 N 5 50 5 -50 5 10257 5 13951 2015 1 4 AS SEA WA GEG WA 1220 62.0 224.0 0 0 0 47.4444 -122.3138 112.8 FM-15 0 5 22000 5 16093 5 N 5 0 5 -44 5 10280 5 47.6216 -117.528 717.2 FM-15 0 5 853 5 12875 5 N 5 -106 5 -122 5 10335 5 13951 2015 1 4 B6 FLL FL BOS MA 1342 188.0 1237.0 0 1 1 26.07875 -80.16217 3.4 FM-15 0 5 1829 5 16093 5 N 5 250 5 206 5 10225 5 42.3606 -71.0097 3.7 FM-15 82 5 22000 5 16093 5 N 5 -11 5 -150 5 10175 5 13951 2015 1 4 B6 LAS NV LGB CA 705 65.0 231.0 0 0 0 36.0719 -115.1634 664.5 FM-15 31 5 5486 5 16093 5 N 5 6 5 -94 5 10169 5 33.8116 -118.1463 9.4 FM-15 0 5 22000 5 8047 5 N 5 28 5 -22 5 10192 5 13951 2015 1 4 DL ATL GA HOU TX 1615 142.0 696.0 0 0 0 33.6301 -84.4418 307.8 FM-15 21 5 1981 5 16093 5 N 5 133 5 -39 5 10254 5 29.63806 -95.28194 13.4 FM-15 46 5 305 5 9656 5 N 5 67 5 56 5 10219 5 13951 2015 1 4 DL BNA TN ATL GA 1200 75.0 214.0 0 0 0 36.11889 -86.68917 182.9 FM-15 21 5 1433 5 16093 5 N 5 6 5 -39 5 10294 5 33.6301 -84.4418 307.8 FM-15 21 5 7010 5 16093 5 N 5 83 5 -28 5 10285 5 13951 2015 1 4 DL LAX CA MCO FL 2225 277.0 2218.0 0 0 0 33.938 -118.3888 29.6 FM-15 0 5 22000 5 16093 5 N 5 100 5 44 5 10207 5 28.4339 -81.325 27.4 FM-15 41 5 61 5 0 A N A 172 5 172 5 10233 5 13951 2015 1 4 DL LAX CA MSY LA 1815 213.0 1670.0 0 0 0 33.938 -118.3888 29.6 FM-15 36 5 22000 5 16093 5 N 5 128 5 28 5 10199 5 29.99691 -90.27751 1.2 FM-16 36 5 884 5 14484 5 N 5 144 5 117 5 99999 9 13951 2015 1 4 DL MCI MO MSP MN 900 86.0 393.0 0 0 0 39.2972 -94.7306 306.3 FM-15 51 5 22000 5 16093 5 N 5 -94 5 -122 5 10249 5 44.8831 -93.2289 265.8 FM-15 51 5 2286 5 16093 5 N 5 -83 5 -122 5 10121 5 13951 2015 1 4 DL PBI FL LGA NY 800 163.0 1035.0 0 0 0 26.6847 -80.0994 5.8 FM-15 0 5 610 5 11265 5 N 5 222 5 211 5 10208 5 40.7792 -73.88 3.4 FM-15 51 5 22000 5 16093 5 

joined_data_3m Shape: 1400798 51

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY DELAY LATITUDE LONGITUDE ELEVATION REPORT_TYPE WND_SPEED WND_SPEED_QUAL CIG_HEIGHT CIG_QUAL VIS_DIST VIS_DIST_QUAL VIS_VAR VIS_VAR_QUAL TEMP TEMP_QUAL DEW_TEMP DEW_TEMP_QUAL SLPRESS SLPRESS_QUAL DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_REPORT_TYPE DEST_WND_SPEED DEST_WND_SPEED_QUAL DEST_CIG_HEIGHT DEST_CIG_QUAL DEST_VIS_DIST DEST_VIS_DIST_QUAL DEST_VIS_VAR DEST_VIS_VAR_QUAL DEST_TEMP DEST_TEMP_QUAL DEST_DEW_TEMP DEST_DEW_TEMP_QUAL DEST_SLPRESS DEST_SLPRESS_QUAL FLIGHTS_PER_DAY 2015 5 5 AA DFW TX AUS TX 2020 67.0 190.0 0 0 0 32.8978 -97.0189 170.7 FM-15 26 5 22000 5 16093 5 N 5 244 5 122 5 10152 5 30.1831 -97.6799 146.3 FM-15 31 5 22000 5 16093 5 N 5 267 5 111 5 10153 5 16927 2015 5 5 AA DFW TX ORD IL 700 146.0 802.0 0 0 0 32.8978 -97.0189 170.7 FM-15 36 5 22000 5 16093 5 N 5 161 5 106 5 10152 5 41.995 -87.9336 201.8 FM-15 26 5 22000 5 16093 5 N 5 33 5 11 5 10203 5 16927 2015 5 5 AA DFW TX SFO CA 905 233.0 1464.0 0 0 0 32.8978 -97.0189 170.7 FM-15 0 5 22000 5 16093 5 N 5 133 5 100 5 10165 5 37.6197 -122.3647 2.4 FM-15 26 5 22000 5 16093 5 N 5 144 5 89 5 10092 5 16927 2015 5 5 AA JFK NY BOS MA 1629 80.0 187.0 0 0 0 40.6386 -73.7622 3.4 FM-15 57 5 1097 5 16093 5 N 5 117 5 44 5 10154 5 42.3606 -71.0097 3.7 FM-15 57 5 7620 5 16093 5 N 5 89 5 39 5 10162 5 16927 2015 5 5 AA LAX CA LAS NV 1640 70.0 236.0 0 0 0 33.938 -118.3888 29.6 FM-15 57 5 5486 5 14484 5 N 5 194 5 128 5 10125 5 36.0719 -115.1634 664.5 FM-15 77 5 7620 5 16093 5 N 5 344 5 -61 5 10071 5 16927 2015 5 5 AA LGA NY MIA FL 1950 189.0 1096.0 0 0 0 40.7792 -73.88 3.4 FM-15 51 5 7620 5 16093 5 N 5 133 5 44 5 10136 5 25.7881 -80.3169 8.8 FM-15 41 5 22000 5 16093 5 N 5 289 5 94 5 10111 5 16927 2015 5 5 AA MCO FL ORD IL 1928 175.0 1005.0 0 0 0 28.4339 -81.325 27.4 FM-15 62 5 22000 5 16093 5 N 5 283 5 106 5 10109 5 41.995 -87.9336 201.8 FM-15 41 5 7620 5 16093 5 N 5 178 5 44 5 10193 5 16927 2015 5 5 AA ORD IL DFW TX 1325 154.0 802.0 0 1 1 41.995 -87.9336 201.8 FM-15 21 5 22000 5 16093 5 N 5 150 5 39 5 10221 5 32.8978 -97.0189 170.7 FM-15 46 5 22000 5 16093 5 N 5 228 5 139 5 10184 5 16927 2015 5 5 AA ORD IL DFW TX 900 163.0 802.0 0 0 0 41.995 -87.9336 201.8 FM-15 31 5 22000 5 16093 5 N 5 67 5 28 5 10214 5 32.8978 -97.0189 170.7 FM-15 0 5 22000 5 16093 5 N 5 133 5 100 5 10165 5 16927 2015 5 5 AS JNU AK ANC AK 1945 96.0 571.0 0 0 0 58.3566 -134.564 4.9 FM-15 57 5 1676 5 16093 5 N 5 94 5 50 5 10155 5 61.169 -150.0278 36.6 FM-15 31 5 7620 5 16093 5 N 5 122 5 6 5 10137 5 16927 2015 5 5 AS ORD IL SEA WA 800 267.0 1721.0 0 0 0 41.995 -87.9336 201.8 FM-15 26 5 22000 5 16093 5 N 5 33 5 17 5 10208 5 47.4444 -122.3138 112.8 FM-15 31 5 6096 5 16093 5 N 5 94 5 61 5 10193 5 16927 2015 5 5 AS SAN CA BOS MA 845 343.0 2588.0 0 0 0 32.7336 -117.1831 4.6 FM-15 0 5 7620 5 14484 5 N 5 172 5 144 5 10111 5 42.3606 -71.0097 3.7 FM-15 15 5 701 5 16093 5 N 5 78 5 44 5 10163 5 16927 2015 5 5 AS SEA WA SNA CA 1400 157.0 978.0 0 0 1 47.4444 -122.3138 112.8 FM-15 36 5 22000 5 16093 5 N 5 156 5 83 5 10189 5 33.68 -117.86639 16.5 FM-15 26 5 7620 5 16093 5 N 5 256 5 111 5 10122 5 16927 2015 5 5 B6 BOS MA EWR NJ 630 83.0 200.0 0 0 0 42.3606 -71.0097 3.7 FM-16 41 5 579 5 16093 5 N 5 70 5 30 5 99999 9 40.6825 -74.1694 2.1 FM-15 36 5 1829 5 16093 5 N 5 100 5 39 5 10132 5 16927 2015 5 5 B6 BOS MA SJU PR 2359 231.0 1674.0 0 0 0 42.3606 -71.0097 3.7 FM-15 31 5 22000 5 16093 5 N 5 56 5 33 5 10164 5 18.4325 -66.01083 2.7 FM-15 21 5 22000 5 16093 5 N 5 278 5 217 5 10150 5 16927 2015 5 5 B6 JFK NY ORD IL 1930 185.0 740.0 0 0 0 40.6386 -73.7622 3.4 FM-15 62 5 7620 5 16093 5 N 5 111 5 44 5 10146 5 41.995 -87.9336 201.8 FM-15 41 5 7620 5 16093 5 N 5 178 5 44 5 10193 5 16927 2015 5 5 DL ATL GA LAS NV 2146 269.0 1747.0 0 0 0 33.6301 -84.4418 307.8 FM-15 57 5 22000 5 16093 5 N 5 206 5 50 5 10150 5 36.0719 -115.1634 664.5 FM-15 93 5 7620 5 16093 5 N 5 344 5 -56 5 10055 5 16927

joined_data Shape: 31534960 51

## Split Data: 

###### Train data:  
3 month data = 1st and 2nd months  
full data = 2015 through 2017  

###### Validation/Test Data: 
3 month data = 3rd month (validation)  
full data = 2018 (validation), 2019 (test)

In [0]:
train_3m        = joined_data_3m.where("MONTH < 3")
valid_test_3m   = joined_data_3m.where("MONTH > 2")
            
train           = joined_data.where("YEAR < 2018")
valid_test      = joined_data.where("YEAR > 2017")

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m", True)      #remove file if there already is an existing one, be careful with this!!!
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m", True)      #remove file if there already is an existing one, be careful with this!!!
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train", True)      #remove file if there already is an existing one, be careful with this!!!
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test", True)      #remove file if there already is an existing one, be careful with this!!!

train_3m.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m")  
valid_test_3m.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m")                                    
train.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train")                                    
valid_test.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test")

In [0]:
#Read Data
train_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m/part-00*.parquet")
valid_test_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test_3m/part-00*.parquet")
print("3-Month Train/Validation/Test:", train_3m.count(), valid_test_3m.count())

train = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train/part-00*.parquet")
valid_test = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/valid_test/part-00*.parquet")
print("Full Data Train/Validation/Test:", train.count(), valid_test.count())

3-Month Train/Validation/Test: 897251 503547
Full Data Train/Validation/Test: 17056263 14478697

# A) Drop rows:  
-Where weather readings are suspect or erroneous   
-Where report_types are SY-MT, FM-16, SOD,SOM  
-Where there are nulls  
-Where there are 99999 (missing) data

#### Dropping 2,3,6,7 Quality in Weather Data (Suspect or Erroneous) & Duplicates

In [0]:
#Drop Suspect or Erroneous weather readings

train_3m.registerTempTable('quality_3m')
train_3m_dropqual = spark.sql("""SELECT * 
                                FROM quality_3m 
                                WHERE 
                                  WND_SPEED_QUAL!='2' and WND_SPEED_QUAL!='3' and WND_SPEED_QUAL!='6' and WND_SPEED_QUAL!='7' and
                                  CIG_QUAL!='2' and CIG_QUAL!='3' and CIG_QUAL!='6' and CIG_QUAL!='7' and
                                  VIS_DIST_QUAL!='2' and VIS_DIST_QUAL!='3' and VIS_DIST_QUAL!='6' and VIS_DIST_QUAL!='7' and
                                  VIS_VAR_QUAL!='2' and VIS_VAR_QUAL!='3' and VIS_VAR_QUAL!='6' and VIS_VAR_QUAL!='7' and
                                  TEMP_QUAL!='2' and TEMP_QUAL!='3' and TEMP_QUAL!='6' and TEMP_QUAL!='7' and
                                  DEW_TEMP_QUAL!='2' and DEW_TEMP_QUAL!='3' and DEW_TEMP_QUAL!='6' and DEW_TEMP_QUAL!='7' and
                                  SLPRESS_QUAL!='2' and SLPRESS_QUAL!='3' and SLPRESS_QUAL!='6' and SLPRESS_QUAL!='7' and
                                  
                                  DEST_WND_SPEED_QUAL!='2' and DEST_WND_SPEED_QUAL!='3' and DEST_WND_SPEED_QUAL!='6' and DEST_WND_SPEED_QUAL!='7' and
                                  DEST_CIG_QUAL!='2' and DEST_CIG_QUAL!='3' and DEST_CIG_QUAL!='6' and DEST_CIG_QUAL!='7' and
                                  DEST_VIS_DIST_QUAL!='2' and DEST_VIS_DIST_QUAL!='3' and DEST_VIS_DIST_QUAL!='6' and DEST_VIS_DIST_QUAL!='7' and
                                  DEST_VIS_VAR_QUAL!='2' and DEST_VIS_VAR_QUAL!='3' and DEST_VIS_VAR_QUAL!='6' and DEST_VIS_VAR_QUAL!='7' and
                                  DEST_TEMP_QUAL!='2' and DEST_TEMP_QUAL!='3' and DEST_TEMP_QUAL!='6' and DEST_TEMP_QUAL!='7' and
                                  DEST_DEW_TEMP_QUAL!='2' and DEST_DEW_TEMP_QUAL!='3' and DEST_DEW_TEMP_QUAL!='6' and DEST_DEW_TEMP_QUAL!='7' and
                                  DEST_SLPRESS_QUAL!='2' and DEST_SLPRESS_QUAL!='3' and DEST_SLPRESS_QUAL!='6' and DEST_SLPRESS_QUAL!='7'                                  
                                """)
train_3m_dropqual = train_3m_dropqual.drop('WND_SPEED_QUAL','CIG_QUAL','VIS_DIST_QUAL','VIS_VAR_QUAL','TEMP_QUAL','DEW_TEMP_QUAL','SLPRESS_QUAL', 'DEST_WND_SPEED_QUAL','DEST_CIG_QUAL','DEST_VIS_DIST_QUAL','DEST_VIS_VAR_QUAL','DEST_TEMP_QUAL','DEST_DEW_TEMP_QUAL','DEST_SLPRESS_QUAL')

#Store Data
file_to_store = train_3m_dropqual                          
filename = "train_3m_dropqual"                     
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

############################################

train.registerTempTable('quality')
train_dropqual = spark.sql("""   SELECT * 
                                FROM quality 
                                WHERE 
                                  WND_SPEED_QUAL!='2' and WND_SPEED_QUAL!='3' and WND_SPEED_QUAL!='6' and WND_SPEED_QUAL!='7' and
                                  CIG_QUAL!='2' and CIG_QUAL!='3' and CIG_QUAL!='6' and CIG_QUAL!='7' and
                                  VIS_DIST_QUAL!='2' and VIS_DIST_QUAL!='3' and VIS_DIST_QUAL!='6' and VIS_DIST_QUAL!='7' and
                                  VIS_VAR_QUAL!='2' and VIS_VAR_QUAL!='3' and VIS_VAR_QUAL!='6' and VIS_VAR_QUAL!='7' and
                                  TEMP_QUAL!='2' and TEMP_QUAL!='3' and TEMP_QUAL!='6' and TEMP_QUAL!='7' and
                                  DEW_TEMP_QUAL!='2' and DEW_TEMP_QUAL!='3' and DEW_TEMP_QUAL!='6' and DEW_TEMP_QUAL!='7' and
                                  SLPRESS_QUAL!='2' and SLPRESS_QUAL!='3' and SLPRESS_QUAL!='6' and SLPRESS_QUAL!='7' and
                                  
                                  DEST_WND_SPEED_QUAL!='2' and DEST_WND_SPEED_QUAL!='3' and DEST_WND_SPEED_QUAL!='6' and DEST_WND_SPEED_QUAL!='7' and
                                  DEST_CIG_QUAL!='2' and DEST_CIG_QUAL!='3' and DEST_CIG_QUAL!='6' and DEST_CIG_QUAL!='7' and
                                  DEST_VIS_DIST_QUAL!='2' and DEST_VIS_DIST_QUAL!='3' and DEST_VIS_DIST_QUAL!='6' and DEST_VIS_DIST_QUAL!='7' and
                                  DEST_VIS_VAR_QUAL!='2' and DEST_VIS_VAR_QUAL!='3' and DEST_VIS_VAR_QUAL!='6' and DEST_VIS_VAR_QUAL!='7' and
                                  DEST_TEMP_QUAL!='2' and DEST_TEMP_QUAL!='3' and DEST_TEMP_QUAL!='6' and DEST_TEMP_QUAL!='7' and
                                  DEST_DEW_TEMP_QUAL!='2' and DEST_DEW_TEMP_QUAL!='3' and DEST_DEW_TEMP_QUAL!='6' and DEST_DEW_TEMP_QUAL!='7' and
                                  DEST_SLPRESS_QUAL!='2' and DEST_SLPRESS_QUAL!='3' and DEST_SLPRESS_QUAL!='6' and DEST_SLPRESS_QUAL!='7'
                                  """)
train_dropqual = train_dropqual.drop('WND_SPEED_QUAL','CIG_QUAL','VIS_DIST_QUAL','VIS_VAR_QUAL','TEMP_QUAL','DEW_TEMP_QUAL','SLPRESS_QUAL', 'DEST_WND_SPEED_QUAL','DEST_CIG_QUAL','DEST_VIS_DIST_QUAL','DEST_VIS_VAR_QUAL','DEST_TEMP_QUAL','DEST_DEW_TEMP_QUAL','DEST_SLPRESS_QUAL')

#Store Data
file_to_store = train_dropqual                          
filename = "train_dropqual"                     
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "train_3m_dropqual"                      
train_3m_dropqual = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_3m_dropqual.display()
# print("train_3m_dropqual Shape:", train_3m_dropqual.count(), len(train_3m_dropqual.columns))

############################################

filename = "train_dropqual"                      
train_dropqual = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_dropqual.display()
# print("train_dropqual Shape:", train_dropqual.count(), len(train_dropqual.columns))

#### Drop Nulls, 99999 (missing data), and specific report_types

In [0]:
#DROP NA/NULL values
train_3m_dropqual_dropna = train_3m_dropqual.na.drop()

#REMOVE THOSE WITH 99999,9999,999 missing values and REPORT_TYPE SY-MT or FM-16
train_3m_dropqual_dropna.registerTempTable('missing_3m')
train_3m_dropqual_dropna_drop99999 = spark.sql("""SELECT * 
                                                  FROM missing_3m 
                                                  WHERE 
                                                  WND_SPEED!=9999 and CIG_HEIGHT!=99999 and 
                                                  VIS_DIST!=999999 and VIS_VAR!='9' and 
                                                  TEMP!=9999 and DEW_TEMP!=9999 and SLPRESS!=99999 and
                                                  REPORT_TYPE != 'SY-MT' and REPORT_TYPE != 'FM-16' and
                                                  REPORT_TYPE != 'SOD' and REPORT_TYPE != 'SOM' and
                                                  
                                                  DEST_WND_SPEED!=9999 and DEST_CIG_HEIGHT!=99999 and 
                                                  DEST_VIS_DIST!=999999 and DEST_VIS_VAR!='9' and 
                                                  DEST_TEMP!=9999 and DEST_DEW_TEMP!=9999 and DEST_SLPRESS!=99999 and
                                                  DEST_REPORT_TYPE != 'SY-MT' and DEST_REPORT_TYPE != 'FM-16' and
                                                  DEST_REPORT_TYPE != 'SOD' and DEST_REPORT_TYPE != 'SOM'                                                  """)

#Store Data
file_to_store = train_3m_dropqual_dropna_drop99999                          
filename = "train_3m_dropqual_dropna_drop99999"                     
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

############################################

#DROP NA/NULL values
train_dropqual_dropna = train_dropqual.na.drop()

#REMOVE THOSE WITH 99999,9999,999 missing values and REPORT_TYPE SY-MT or FM-16
train_dropqual_dropna.registerTempTable('missing')
train_dropqual_dropna_drop99999 = spark.sql("""SELECT * 
                                                  FROM missing 
                                                  WHERE 
                                                  WND_SPEED!=9999 and CIG_HEIGHT!=99999 and 
                                                  VIS_DIST!=999999 and VIS_VAR!='9' and 
                                                  TEMP!=9999 and DEW_TEMP!=9999 and SLPRESS!=99999 and
                                                  REPORT_TYPE != 'SY-MT' and REPORT_TYPE != 'FM-16' and
                                                  REPORT_TYPE != 'SOD' and REPORT_TYPE != 'SOM' and
                                                  
                                                  DEST_WND_SPEED!=9999 and DEST_CIG_HEIGHT!=99999 and 
                                                  DEST_VIS_DIST!=999999 and DEST_VIS_VAR!='9' and 
                                                  DEST_TEMP!=9999 and DEST_DEW_TEMP!=9999 and DEST_SLPRESS!=99999 and
                                                  DEST_REPORT_TYPE != 'SY-MT' and DEST_REPORT_TYPE != 'FM-16' and
                                                  DEST_REPORT_TYPE != 'SOD' and DEST_REPORT_TYPE != 'SOM'                                                  """)

#Store Data
file_to_store = train_dropqual_dropna_drop99999                          
filename = "train_dropqual_dropna_drop99999"                     
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "train_3m_dropqual_dropna_drop99999"                      
train_3m_dropqual_dropna_drop99999 = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_3m_dropqual_dropna_drop99999.display()
# print("train_3m_dropqual_dropna_drop99999 Shape:", train_3m_dropqual_dropna_drop99999.count(), len(train_3m_dropqual_dropna_drop99999.columns))

############################################

filename = "train_dropqual_dropna_drop99999"                      
train_dropqual_dropna_drop99999 = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_dropqual_dropna_drop99999.display()
# print("train train_dropqual_dropna_drop99999:", train_dropqual_dropna_drop99999.count(), len(train_dropqual_dropna_drop99999.columns))

In [0]:
# Error Checking

# #COUNT (to check size of each dataset and choose which dataset to keep)
print("{:60s}\t| {:10s}\t| {}".format("Data","Rows","Columns"))
print("{:60s}\t| {:10d}\t| {}".format("train_3m",train_3m.count(),len(train_3m.columns)))
print("{:60s}\t| {:10d}\t| {}".format("train_3m_dropqual",train_3m_dropqual.count(),len(train_3m_dropqual.columns)))
print("{:60s}\t| {:10d}\t| {}".format("train_3m_dropqual_dropna",train_3m_dropqual_dropna.count(),len(train_3m_dropqual_dropna.columns)))
print("{:60s}\t| {:10d}\t| {}".format("train_3m_dropqual_dropna_drop99999",train_3m_dropqual_dropna_drop99999.count(),len(train_3m_dropqual_dropna_drop99999.columns)))

print("{:60s}\t| {:10s}\t| {}".format("Data","Rows","Columns"))
print("{:60s}\t| {:10d}\t| {}".format("train",train.count(),len(train.columns)))
print("{:60s}\t| {:10d}\t| {}".format("train_dropqual",train_dropqual.count(),len(train_dropqual.columns)))
print("{:60s}\t| {:10d}\t| {}".format("train_dropqual_dropna",train_dropqual_dropna.count(),len(train_dropqual_dropna.columns)))
print("{:60s}\t| {:10d}\t| {}".format("train_dropqual_dropna_drop99999",train_dropqual_dropna_drop99999.count(),len(train_dropqual_dropna_drop99999.columns)))

# 1) train_3m   (no changes)
# 2) train_3m_dropqual  (drop suspect or erroneous data and some stations like MOD, SOD, FM-16)
# 3) train_3m_dropqual_dropna (drop na/nulls)
# 4) train_3m_dropqual_dropna_drop99999 (drop 99999 missing data)

Data | Rows | Columns
train_3m | 897251	| 51
train_3m_dropqual | 892664	| 37
train_3m_dropqual_dropna | 892662	| 37
train_3m_dropqual_dropna_drop99999 | 753364	| 37
Data | Rows | Columns
train | 17056263	| 51
train_dropqual | 16974943	| 37
train_dropqual_dropna | 16974924	| 37
train_dropqual_dropna_drop99999 | 14771645	| 37

# B) Bin Data

Add code for creating bins for these features:

AIRLINE DATA:

Departure time (* Should be based on local time - this binning needs to occur before UTC)
* 0 - 1:59
* 2 - 3:59
* 4 - 5:59
* 6 - 7:59
* 8 - 9:59
* 10 - 11:59
* 12 - 13:59 
* 14 - 15:59 
* 16 - 17:59
* 18 - 19:59
* 20 - 21:59
* 22 - 23:59


WEATHER DATA:

Sky condition (CIG_HEIGHT)
* 0 - 21999 = Limited vertical visibility
* 22000 = Unlimited veritcal visibility

Wind Speed (based on Beaufort Scale: https://en.wikipedia.org/wiki/Beaufort_scale)
* <15 = Calm to light breeze
* <33 = Gentle breeze
* <107 = Moderate to fresh breeze
* \>=138 = Strong breeze to gale/storm

Visibility Distance
* \>= 16093 (>= 10 miles) --- most values are exactly 16093, likely indicating max visibility
* < 16093 (< 10 miles) --- group all other values below together

In [0]:
# 3 Month Data

# change data to whatever the processed and joined dataframe is called
data_3m = train_3m_dropqual_dropna_drop99999.withColumn('CRS_DEP_TIME',train_3m_dropqual_dropna_drop99999.CRS_DEP_TIME.cast(FloatType()) )

#Convert departure time to bins
dep_time_buck_3m = Bucketizer(splits=[ 0, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000, 2200, float('Inf') ],inputCol="CRS_DEP_TIME", outputCol="CRS_DEP_TIME_BUCK")
air_buck_3m = dep_time_buck_3m.setHandleInvalid("keep").transform(data_3m)

#Convert wind, vis, sky to bins  (First for origin weather)
wind_buck_3m = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="WND_SPEED", outputCol="WND_SPEED_BUCK")
vis_buck_3m = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="VIS_DIST", outputCol="VIS_DIST_BUCK")
sky_buck_3m = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="CIG_HEIGHT", outputCol="CIG_HEIGHT_BUCK")
w_buck_3m = wind_buck_3m.setHandleInvalid("keep").transform(air_buck_3m)   
w_buck_3m = vis_buck_3m.setHandleInvalid("keep").transform(w_buck_3m)
w_buck_3m = sky_buck_3m.setHandleInvalid("keep").transform(w_buck_3m)

#Convert wind, vis, sky to bins  (First for destination weather)
wind_buck_3m_dw = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="DEST_WND_SPEED", outputCol="DEST_WND_SPEED_BUCK")
vis_buck_3m_dw = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="DEST_VIS_DIST", outputCol="DEST_VIS_DIST_BUCK")
sky_buck_3m_dw = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="DEST_CIG_HEIGHT", outputCol="DEST_CIG_HEIGHT_BUCK")
w_buck_3m = wind_buck_3m_dw.setHandleInvalid("keep").transform(w_buck_3m)   
w_buck_3m = vis_buck_3m_dw.setHandleInvalid("keep").transform(w_buck_3m)
w_buck_3m = sky_buck_3m_dw.setHandleInvalid("keep").transform(w_buck_3m)

# w_buck_3m.display()
# print("w_buck_3m shape:", w_buck_3m.count(), len(w_buck_3m.columns))
# print(w_buck_3m.columns)

#####################################
# Full Data

# change data to whatever the processed and joined dataframe is called
data = train_dropqual_dropna_drop99999.withColumn('CRS_DEP_TIME',train_dropqual_dropna_drop99999.CRS_DEP_TIME.cast(FloatType()) )

# #Convert departure time to bins (old binning, update to more bins below)
# dep_time_buck = Bucketizer(splits=[ 0, 400, 800, 1200, 1600, 2000, float('Inf') ],inputCol="CRS_DEP_TIME", outputCol="CRS_DEP_TIME_BUCK")
# air_buck = dep_time_buck.setHandleInvalid("keep").transform(data)

#Convert departure time to bins 
dep_time_buck = Bucketizer(splits=[ 0, 200, 400, 600, 800, 1000, 1200, 1400, 1600, 1800, 2000, 2200, float('Inf') ],inputCol="CRS_DEP_TIME", outputCol="CRS_DEP_TIME_BUCK")
air_buck = dep_time_buck.setHandleInvalid("keep").transform(data)

#Convert wind, vis, sky to bins  (First for origin weather)
wind_buck = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="WND_SPEED", outputCol="WND_SPEED_BUCK")
vis_buck = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="VIS_DIST", outputCol="VIS_DIST_BUCK")
sky_buck = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="CIG_HEIGHT", outputCol="CIG_HEIGHT_BUCK")
w_buck = wind_buck.setHandleInvalid("keep").transform(air_buck)   
w_buck = vis_buck.setHandleInvalid("keep").transform(w_buck)
w_buck = sky_buck.setHandleInvalid("keep").transform(w_buck)

#Convert wind, vis, sky to bins  (First for destination weather)
wind_buck_dw = Bucketizer(splits=[ 0, 15, 33, 107, float('Inf') ],inputCol="DEST_WND_SPEED", outputCol="DEST_WND_SPEED_BUCK")
vis_buck_dw = Bucketizer(splits=[ 0, 16092, float('Inf') ],inputCol="DEST_VIS_DIST", outputCol="DEST_VIS_DIST_BUCK")
sky_buck_dw = Bucketizer(splits=[ 0, 21999, float('Inf') ],inputCol="DEST_CIG_HEIGHT", outputCol="DEST_CIG_HEIGHT_BUCK")
w_buck = wind_buck_dw.setHandleInvalid("keep").transform(w_buck)   
w_buck = vis_buck_dw.setHandleInvalid("keep").transform(w_buck)
w_buck = sky_buck_dw.setHandleInvalid("keep").transform(w_buck)

# w_buck.display()
# print("w_buck shape:", w_buck.count(), len(w_buck.columns))
# print(w_buck.columns)

In [0]:
# drop numeric columns (keep only features needed for modeling)

##########################
# 3 MONTH DATA

train_data_buck_3m = w_buck_3m.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'CRS_DEP_TIME_BUCK', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'FLIGHTS_PER_DAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED_BUCK', 'CIG_HEIGHT_BUCK', 'VIS_DIST_BUCK', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS', 'DEST_WND_SPEED_BUCK', 'DEST_VIS_DIST_BUCK', 'DEST_CIG_HEIGHT_BUCK', 'DELAY')

#SAVING Spark Dataframe to Shared Directory
# dbutils.fs.mkdirs("dbfs:/mnt/mids-w261/team_25/")               #Made Directory in DataBricks, no need to remake
file_to_store = train_data_buck_3m                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data_buck_3m"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

###########################
#FULL DATA

train_data_buck = w_buck.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'CRS_DEP_TIME_BUCK', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'FLIGHTS_PER_DAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED_BUCK', 'CIG_HEIGHT_BUCK', 'VIS_DIST_BUCK', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS', 'DEST_WND_SPEED_BUCK', 'DEST_VIS_DIST_BUCK', 'DEST_CIG_HEIGHT_BUCK', 'DELAY')

#SAVING Spark Dataframe to Shared Directory
# dbutils.fs.mkdirs("dbfs:/mnt/mids-w261/team_25/")               #Made Directory in DataBricks, no need to remake
file_to_store = train_data_buck                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data_buck"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "train_data_buck_3m"                      
train_data_buck_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_data_buck_3m.display()
# print("train_data_buck_3m Shape:", train_data_buck_3m.count(), len(train_data_buck_3m.columns))

############################################

filename = "train_data_buck"                      
train_data_buck = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_data_buck.display()
# print("train_data_buck:", train_data_buck.count(), len(train_data_buck.columns))

# C) Use train data to create Airport PageRank helper Table   
(this will be used to join with both training and validation/test data)  

Airport Page Rank
Steps:  
1) Create graph of airports based on all the flights (origin to destination).  
2) Calculate the page rank of the airports.

In [0]:
#Reading Training Data from previous cell
filename = "train_data_buck"                         #CHANGE THIS: file name in database (to open)
train_data_buck = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")

train_data_buck.registerTempTable("full_tt")
airports_train_PR = spark.sql("SELECT ORIGIN, DEST FROM full_tt WHERE YEAR < 2018")

#SAVING Spark Dataframe to Shared Directory
file_to_store = airports_train_PR                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "airports_train_PR"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "airports_train_PR"                      
airports_train_PR = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# airports_train_PR.display()

In [0]:
#All Functions To Create a Graph and Calculate Page Rank

from pyspark.accumulators import AccumulatorParam

class FloatAccumulatorParam(AccumulatorParam):
    """
    Custom accumulator for use in page rank to keep track of various masses.
    
    IMPORTANT: accumulators should only be called inside actions to avoid duplication.
    We stringly recommend you use the 'foreach' action in your implementation below.
    """
    def zero(self, value):
        return value
    def addInPlace(self, val1, val2):
        return val1 + val2

def parse(line):
  return (line[0], (0,{line[1]:1}))

def get_adj_list(x, y):
  return (0, {k: x[1].get(k, 0) + y[1].get(k, 0) for k in set(x[1]) | set(y[1])})
      
def initGraph(dataRDD):
    """
    Spark job to read in the raw data and initialize an 
    adjacency list representation with a record for each
    node (including dangling nodes).
    
    Returns: 
        graphRDD -  a pair RDD of (node_id , (score, edges))
    """
#     def parse(line):
#         node, edges = line.split('\t')
#         return (node, (1, ast.literal_eval(edges)))
   
    #parse original graph data
    ogRDD = dataRDD.cache()
        
    # produce RDD of individual nodes - use indicator 0 if already a node in adjacency list, 1 if in an edge list
    # reduce by multiplying - dangling nodes will still have indicator 1 after reducing
    graphRDD = dataRDD.flatMap(lambda x: ({(x[0], 0)}, {(i, 1) for i in x[1][1].keys()})) \
                    .flatMap(lambda x: x) \
                    .reduceByKey(lambda x,y: x*y) \
                    .filter(lambda x: x[1] == 1) \
                    .map(lambda x: (x[0], (1, dict()))) \
                    .union(ogRDD) \
                    .cache()
  
    # count total nodes
    N = graphRDD.count()
    rank = sc.broadcast(1.0/N)
    graphRDD = graphRDD.map(lambda x: (x[0], (rank.value, x[1][1])))
    
    return graphRDD


def runPageRank(graphInitRDD, alpha = 0.15, maxIter = 10, verbose = True):
    """
    Spark job to implement page rank
    Args: 
        graphInitRDD  - pair RDD of (node_id , (score, edges))
        alpha         - (float) teleportation factor
        maxIter       - (int) stopping criteria (number of iterations)
        verbose       - (bool) option to print logging info after each iteration
    Returns:
        steadyStateRDD - pair RDD of (node_id, pageRank)
    """
    # teleportation:
    a = sc.broadcast(alpha)
    
    # damping factor:
    d = sc.broadcast(1-a.value)
    
    # initialize accumulators for dangling mass & total mass
    mmAccum = sc.accumulator(0.0, FloatAccumulatorParam())
    totAccum = sc.accumulator(0.0, FloatAccumulatorParam())

    def pageRankMap(node, rank, edges):
        """
        yields partial mass distributed to each node with edge list
        yields original node and edge list
        """
        num_outlinks = sum(edges.values())
        for link, freq in edges.items():
            yield (link, (rank / num_outlinks * freq, dict()))
        yield (node, (0, edges))
        
    def pageRankReduce(line1, line2):
        """
        adds masses together for each receiving node to get full partial mass
        """
        line1[1].update(line2[1])
        return (line1[0]+line2[0], line1[1])
      
    def pageRankMap2(rank, edges, mm):
        """
        distributes dangling mass and teleportation factor
        returns PageRank and edge list for the given node
        """
        new_rank = (a.value/n.value) + d.value*((mm/n.value) + rank)
        return (new_rank, edges)
      
    def incrementAcc(line, acc):
        """
        increments a given accumulator by the PageRank
        """
        acc += line[1][0]
        
    
    # calculate total number of nodes for use distributing down the line
    nodes = graphInitRDD.count()
    n = sc.broadcast(nodes)

    # 1st map reduce job to find partial pagerank
    steadyStateRDD = graphInitRDD
    for iteration in range(nIter):
  
        mmAccum.value = 0
        dangNodes = steadyStateRDD.filter(lambda x: len(x[1][1]) == 0) \
                                  .foreach(lambda x: incrementAcc(x, mmAccum))
        
        if verbose:
            print(f"Iteration #{iteration+1}")
            print(f"Missing Mass: {mmAccum}")
      
        # return partial masses 
        steadyStateRDD = steadyStateRDD.flatMap(lambda x: pageRankMap(x[0], x[1][0], x[1][1])) \
                               .reduceByKey(lambda x,y: pageRankReduce(x,y))

        # 2nd map reduce job to add in dangling mass and teleportation
        mm = mmAccum.value
        steadyStateRDD = steadyStateRDD.mapValues(lambda x: pageRankMap2(x[0], x[1], mm))
        
        # calculate, print and reset total mass accumulator      
        steadyStateRDD.foreach(lambda x: incrementAcc(x, totAccum))
        if verbose:
            print(f"Total Mass: {totAccum}\n")
        totAccum.value = 0
                  
#     steadyStateRDD = steadyStateRDD.mapValues(lambda x: x[0])
    
    return steadyStateRDD

In [0]:
#Make RDD from Spark Dataframe for Page Rank Code
RDD1 = airports_train_PR.rdd
  
#Process RDD1 to format for Creating a Graph
RDD2 = RDD1.map(lambda x: parse(x)).reduceByKey(lambda x, y: get_adj_list(x, y)).cache() 
#RDD2.take(2)

#Create Graph Structure
graphInit = initGraph(RDD2).cache()
# graphInit.take(3)

#Do Page Rank 
nIter = 20
airportPR = runPageRank(graphInit, alpha = 0.15, maxIter = nIter, verbose = False).cache()
airportPR_ordered = airportPR.map(lambda x: (x[0], x[1][0])).takeOrdered(500, key=lambda x: - x[1])

#Convert to dataframe, rename columns
airportPR_ordered_df = spark.createDataFrame(airportPR_ordered)
airportPR_ordered_df = airportPR_ordered_df.withColumnRenamed('_1','original')
airportPR_ordered_df = airportPR_ordered_df.withColumnRenamed('_2','pagerank')

#SAVING Spark Dataframe to Shared Directory
file_to_store = airportPR_ordered_df                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "airportPR_ordered_df"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "airportPR_ordered_df"                      
airportPR_ordered_df = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
airportPR_ordered_df.display()

original pagerank ANC 0.008173654734974205 HOU 0.00791432725862876 STL 0.0076554971275557965 BNA 0.007388492133732665 OAK 0.006969406014494394 AUS 0.006677432434648058 RNO 0.0025098286770367387 TUL 0.0024881541004467328 MEM 0.002476896423479847 KOA 0.0024295265636139077 CHS 0.0022642713779227946 LGB 0.0021726026673556387 VPS 0.0010311674860085463 PIA 0.0010195976319418711 BIL 0.0010009554500324254 EUG 0.0010008411943344168 PSC 9.984904738759215E-4 OME 9.761318808890393E-4 YUM 7.199764886790682E-4 EYW 7.197534603064892E-4 PSG 7.157598423253558E-4 SPI 7.090846023298813E-4 CLL 7.078269070337451E-4 AVP 7.04720002349563E-4 CKB 4.812991207689215E-4 ILG 4.802921386251596E-4 ADK 4.793732671093856E-4 STC 4.7924732227255324E-4 SPN 4.770184133755923E-4 SWO 4.76237037485172E-4 FAI 0.0013262672199081918 MAF 0.0013063815649116644 CID 0.0013050452198616414 JAN 0.0013003975214069925 SHV 0.0012990082045643003 MHT 0.001287314833073603 TYR 6.127062195311708E-4 MTJ 6.09565957113867E-4 SGU 6.048695276620925E-4 SPS 6.043368590928946E-4 RDD 6.034296410844161E-4 LWS 6.019344168711308E-4 JAC 5.404110746909291E-4 COD 5.382378279271398E-4 TOL 5.355971075968793E-4 GGG 5.318218512606684E-4 ALO 5.314444110325482E-4 SMX 5.27225302144E-4 MFE 8.323403303765417E-4 HRL 8.289280080042082E-4 BFL 8.277729238115126E-4 AGS 8.247055865650812E-4 MRY 8.178348109971392E-4 HIB 8.164025442580423E-4 ATL 0.06178103047926055 ORD 0.04737763713846122 DFW 0.03817073608327177 DEN 0.03621702748797421 LAX 0.03087132783443129 SFO 0.026173769929446686 PHX 0.024475199961382168 MSP 0.0228724306628863 IAH 0.02232401241556353 SEA 0.022200771421814543 SLC 0.021316208378312395 LAS 0.02129887021282643 DTW 0.02061755116491139 MCO 0.017664227166298715 BOS 0.016488988638580226 EWR 0.016227158507187554 CLT 0.015388660893576225 JFK 0.014589032926165355 LGA 0.014125221879033551 BWI 0.013487763867768883 FLL 0.012174883582663549 MDW 0.012017125493247557 SAN 0.010993872150786075 DCA 0.010509557105859428 MIA 0.010211556958918115 PHL 0.01010704715997805 TPA 0.009735873905956583 DAL 0.00947705481326266 HNL 0.009074163773956763 PDX 0.00860241859146984 SJC 0.006585447900909955 SMF 0.006311131623833591 MCI 0.006284723056427569 MSY 0.00615147191866828 SNA 0.006117821202967675 IAD 0.0054061753716854255 RDU 0.005151502521536252 CLE 0.005018994725322772 MKE 0.004783079391649531 SAT 0.004656858061556915 RSW 0.0043422586671603165 OGG 0.004090420807356113 SJU 0.004081937236125759 IND 0.004076538833610215 PIT 0.003938647433177683 PBI 0.0037684605603798315 CMH 0.0036139633042141924 BUR 0.0034548376150563198 JNU 0.003353090322955504 ONT 0.003223318242525211 ABQ 0.0031813102478444218 JAX 0.0028488264036378554 BUF 0.0027382174329873216 OKC 0.0026952764990530766 TUS 0.0026847997308403464 RIC 0.0026599666862778216 BOI 0.0025605477519756283 PVD 0.002045963964120417 GEG 0.0020179211036701963 GRR 0.00195485288158604 ORF 0.0018830828949039614 PSP 0.001860338533866305 SDF 0.0018106740894036637 MSN 0.001750240176044225 LIT 0.001738491083979504 COS 0.0016775052628886368 DSM 0.0016615927312926414 FAT 0.0016486616670769764 ICT 0.0016411564980797976 ALB 0.0016379189456087048 SAV 0.001529360239480589 KTN 0.001521595152215928 TYS 0.001489100087357839 ROC 0.0014879879200592801 DAY 0.0014854468412440324 HPN 0.0014758822288302648 ITO 0.0014549639067714336 XNA 0.0014493859525682741 CAK 0.0012845971018132629 LEX 0.0012730475771310658 SYR 0.0012729360874187121 PNS 0.0012701878872924048 SBA 0.0012659783054433716 PWM 0.0012316060545819261 FSD 0.0011862424467512394 YAK 0.001178328556230985 BRW 0.0011709442492179724 TTN 0.0011528163929051094 BZN 0.001142048311936825 GRB 0.001136846402582511 CDV 0.001132880654916345 MOB 0.001131451668123938 CAE 0.0011290377093376397 FAR 0.001114313841460956 CHA 0.0011129443814830672 ASE 0.0010927110161721662 HSV 0.0010807382141694542 ISP 0.0010774759297066173 FNT 0.001063680536137017 ECP 0.001063637610786967 JMS 0.0010592589364223158 LBB 0.001058387502388213 MEI 0.0010546896213114026 SGF 0.00105173897909057

# D) Join Airport PageRank to final table

In [0]:
#Read Data
filename = "train_data_buck_3m"                      
train_data_buck_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_data_buck_3m.display()
# print("train_data_buck_3m Shape:", train_data_buck_3m.count(), len(train_data_buck_3m.columns))
train_data_buck_3m.registerTempTable("train_data_buck_3m_tt")

############################################

filename = "train_data_buck"                      
train_data_buck = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_data_buck.display()
# print("train_data_buck:", train_data_buck.count(), len(train_data_buck.columns))
train_data_buck.registerTempTable("train_data_buck_tt")


In [0]:
#Join Data
airportPR_ordered_df.registerTempTable("airportPR_ordered_df_tt")

# 3 MONTH DATA LEFT JOIN
train_data_3m_dw_b = spark.sql("""SELECT * 
                                FROM train_data_buck_3m_tt t1
                                LEFT JOIN airportPR_ordered_df_tt t2
                                ON (t1.ORIGIN = t2.original)
                                """).drop("original")

train_data_3m_dw_b = train_data_3m_dw_b.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'CRS_DEP_TIME_BUCK', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'FLIGHTS_PER_DAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED_BUCK', 'CIG_HEIGHT_BUCK', 'VIS_DIST_BUCK', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'PAGERANK', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS', 'DEST_WND_SPEED_BUCK', 'DEST_VIS_DIST_BUCK', 'DEST_CIG_HEIGHT_BUCK', 'DELAY')

#SAVING Spark Dataframe to Shared Directory
file_to_store = train_data_3m_dw_b                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data_3m_dw_b"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

############################################

# FULL DATA LEFT JOIN
train_data_dw_b = spark.sql("""SELECT * 
                                FROM train_data_buck_tt t1
                                LEFT JOIN airportPR_ordered_df_tt t2
                                ON (t1.ORIGIN = t2.original)
                                """)

train_data_dw_b = train_data_dw_b.select('YEAR', 'MONTH', 'DAY_OF_WEEK', 'OP_UNIQUE_CARRIER', 'ORIGIN', 'ORIGIN_STATE_ABR', 'DEST', 'DEST_STATE_ABR', 'CRS_DEP_TIME_BUCK', 'CRS_ELAPSED_TIME', 'DISTANCE', 'FIRST_DEP', 'PREVIOUS_DELAY', 'FLIGHTS_PER_DAY', 'LATITUDE', 'LONGITUDE', 'ELEVATION', 'WND_SPEED_BUCK', 'CIG_HEIGHT_BUCK', 'VIS_DIST_BUCK', 'VIS_VAR', 'TEMP', 'DEW_TEMP', 'SLPRESS', 'PAGERANK', 'DEST_LATITUDE', 'DEST_LONGITUDE', 'DEST_ELEVATION', 'DEST_VIS_VAR', 'DEST_TEMP', 'DEST_DEW_TEMP', 'DEST_SLPRESS', 'DEST_WND_SPEED_BUCK', 'DEST_VIS_DIST_BUCK', 'DEST_CIG_HEIGHT_BUCK', 'DELAY')

#SAVING Spark Dataframe to Shared Directory
file_to_store = train_data_dw_b                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data_dw_b"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read Data
filename = "train_data_3m_dw_b"                      
train_data_3m_dw_b = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_data_3m_dw_b.display()
# print("train_data_3m_dw_b Shape:", train_data_3m_dw_b.count(), len(train_data_3m_dw_b.columns))

############################################

filename = "train_data_dw_b"                      
train_data_dw_b = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_data_dw_b.display()
# print("train_data_dw_b:", train_data_dw_b.count(), len(train_data_dw_b.columns))

# E) Create helper table for imputing validation data
(Averages grouped by day_of_week and origin)

In [0]:
#Read Data
filename = "train_3m_dropqual_dropna_drop99999"                      
train_3m_dropqual_dropna_drop99999 = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_3m_dropqual_dropna_drop99999.display()
# print("train_3m_dropqual_dropna_drop99999 Shape:", train_3m_dropqual_dropna_drop99999.count(), len(train_3m_dropqual_dropna_drop99999.columns))

############################################

filename = "train_dropqual_dropna_drop99999"                      
train_dropqual_dropna_drop99999 = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
# train_dropqual_dropna_drop99999.display()
# print("train train_dropqual_dropna_drop99999:", train_dropqual_dropna_drop99999.count(), len(train_dropqual_dropna_drop99999.columns))

In [0]:
#Fix Schema

#3 month data
train_3m_dropqual_dropna_drop99999 = train_3m_dropqual_dropna_drop99999.withColumn('DAY_OF_WEEK',train_3m_dropqual_dropna_drop99999.DAY_OF_WEEK.cast(IntegerType()) )
train_3m_dropqual_dropna_drop99999 = train_3m_dropqual_dropna_drop99999.withColumn('FIRST_DEP',train_3m_dropqual_dropna_drop99999.FIRST_DEP.cast(IntegerType()) )
train_3m_dropqual_dropna_drop99999 = train_3m_dropqual_dropna_drop99999.withColumn('PREVIOUS_DELAY',train_3m_dropqual_dropna_drop99999.PREVIOUS_DELAY.cast(IntegerType()) )
train_3m_dropqual_dropna_drop99999 = train_3m_dropqual_dropna_drop99999.withColumn('CRS_DEP_TIME',train_3m_dropqual_dropna_drop99999.CRS_DEP_TIME.cast(IntegerType()) )

#full data
train_dropqual_dropna_drop99999 = train_dropqual_dropna_drop99999.withColumn('DAY_OF_WEEK',train_dropqual_dropna_drop99999.DAY_OF_WEEK.cast(IntegerType()) )
train_dropqual_dropna_drop99999 = train_dropqual_dropna_drop99999.withColumn('FIRST_DEP',train_dropqual_dropna_drop99999.FIRST_DEP.cast(IntegerType()) )
train_dropqual_dropna_drop99999 = train_dropqual_dropna_drop99999.withColumn('PREVIOUS_DELAY',train_dropqual_dropna_drop99999.PREVIOUS_DELAY.cast(IntegerType()) )
train_dropqual_dropna_drop99999 = train_dropqual_dropna_drop99999.withColumn('CRS_DEP_TIME',train_dropqual_dropna_drop99999.CRS_DEP_TIME.cast(IntegerType()) )

#####################################################################

#Group Data for Averaging. These values will be imputed onto the validation/test data where necessary (bad or missing data)

# 3 MONTH DATA, grouped on day of week and origin
train_3m_groupby = train_3m_dropqual_dropna_drop99999.groupby("DAY_OF_WEEK", "ORIGIN").agg(
                                        avg_('DAY_OF_WEEK').alias("avg_DAY_OF_WEEK"),
                                        avg_('CRS_DEP_TIME').alias("avg_CRS_DEP_TIME"),
                                        avg_('CRS_ELAPSED_TIME').alias("avg_CRS_ELAPSED_TIME"),
                                        avg_('DISTANCE').alias("avg_DISTANCE"),
                                        min_('FIRST_DEP').alias("min_FIRST_DEP"),
                                        min_('PREVIOUS_DELAY').alias("min_PREVIOUS_DELAY"),
                                        avg_('LATITUDE').alias("avg_LATITUDE"),
                                        avg_('LONGITUDE').alias("avg_LONGITUDE"),
                                        avg_('ELEVATION').alias("avg_ELEVATION"),
                                        avg_('WND_SPEED').alias("avg_WND_SPEED"),
                                        avg_('CIG_HEIGHT').alias("avg_CIG_HEIGHT"),
                                        avg_('VIS_DIST').alias("avg_VIS_DIST"),
                                        avg_('TEMP').alias("avg_TEMP"),
                                        avg_('DEW_TEMP').alias("avg_DEW_TEMP"),
                                        avg_('SLPRESS').alias("avg_SLPRESS"),
  
                                        avg_('DEST_LATITUDE').alias("avg_DEST_LATITUDE"),
                                        avg_('DEST_LONGITUDE').alias("avg_DEST_LONGITUDE"),
                                        avg_('DEST_ELEVATION').alias("avg_DEST_ELEVATION"),
                                        avg_('DEST_WND_SPEED').alias("avg_DEST_WND_SPEED"),
                                        avg_('DEST_CIG_HEIGHT').alias("avg_DEST_CIG_HEIGHT"),
                                        avg_('DEST_VIS_DIST').alias("avg_DEST_VIS_DIST"),
                                        avg_('DEST_TEMP').alias("avg_DEST_TEMP"),
                                        avg_('DEST_DEW_TEMP').alias("avg_DEST_DEW_TEMP"),
                                        avg_('DEST_SLPRESS').alias("avg_DEST_SLPRESS")  )

train_3m_groupby=train_3m_groupby.withColumnRenamed("DAY_OF_WEEK", "DOW")
train_3m_groupby=train_3m_groupby.withColumnRenamed("ORIGIN", "O")

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m_groupby", True)      #remove file if there already is an existing one, be careful with this!!!
train_3m_groupby.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m_groupby")  

#################################

# FULL DATA, grouped on month and origin
train_groupby = train_dropqual_dropna_drop99999.groupby("MONTH", "ORIGIN").agg(
                                        avg_('DAY_OF_WEEK').alias("avg_DAY_OF_WEEK"),
                                        avg_('CRS_DEP_TIME').alias("avg_CRS_DEP_TIME"),
                                        avg_('CRS_ELAPSED_TIME').alias("avg_CRS_ELAPSED_TIME"),
                                        avg_('DISTANCE').alias("avg_DISTANCE"),
                                        min_('FIRST_DEP').alias("min_FIRST_DEP"),
                                        min_('PREVIOUS_DELAY').alias("min_PREVIOUS_DELAY"),
                                        avg_('LATITUDE').alias("avg_LATITUDE"),
                                        avg_('LONGITUDE').alias("avg_LONGITUDE"),
                                        avg_('ELEVATION').alias("avg_ELEVATION"),
                                        avg_('WND_SPEED').alias("avg_WND_SPEED"),
                                        avg_('CIG_HEIGHT').alias("avg_CIG_HEIGHT"),
                                        avg_('VIS_DIST').alias("avg_VIS_DIST"),
                                        avg_('TEMP').alias("avg_TEMP"),
                                        avg_('DEW_TEMP').alias("avg_DEW_TEMP"),
                                        avg_('SLPRESS').alias("avg_SLPRESS"),
  
                                        avg_('DEST_LATITUDE').alias("avg_DEST_LATITUDE"),
                                        avg_('DEST_LONGITUDE').alias("avg_DEST_LONGITUDE"),
                                        avg_('DEST_ELEVATION').alias("avg_DEST_ELEVATION"),
                                        avg_('DEST_WND_SPEED').alias("avg_DEST_WND_SPEED"),
                                        avg_('DEST_CIG_HEIGHT').alias("avg_DEST_CIG_HEIGHT"),
                                        avg_('DEST_VIS_DIST').alias("avg_DEST_VIS_DIST"),
                                        avg_('DEST_TEMP').alias("avg_DEST_TEMP"),
                                        avg_('DEST_DEW_TEMP').alias("avg_DEST_DEW_TEMP"),
                                        avg_('DEST_SLPRESS').alias("avg_DEST_SLPRESS")        )

train_groupby=train_groupby.withColumnRenamed("MONTH", "MO")
train_groupby=train_groupby.withColumnRenamed("ORIGIN", "O")

#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_groupby", True)      #remove file if there already is an existing one, be careful with this!!!
train_groupby.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_groupby")  

In [0]:
#Read Data

# 3 MONTH DATA
train_3m_groupby = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_3m_groupby/part-00*.parquet")
train_3m_groupby.display()

#FULL DATA
train_groupby = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/train_groupby/part-00*.parquet")
train_groupby.display()

DOW O avg_DAY_OF_WEEK avg_CRS_DEP_TIME avg_CRS_ELAPSED_TIME avg_DISTANCE min_FIRST_DEP min_PREVIOUS_DELAY avg_LATITUDE avg_LONGITUDE avg_ELEVATION avg_WND_SPEED avg_CIG_HEIGHT avg_VIS_DIST avg_TEMP avg_DEW_TEMP avg_SLPRESS avg_DEST_LATITUDE avg_DEST_LONGITUDE avg_DEST_ELEVATION avg_DEST_WND_SPEED avg_DEST_CIG_HEIGHT avg_DEST_VIS_DIST avg_DEST_TEMP avg_DEST_DEW_TEMP avg_DEST_SLPRESS 1 ATL 1.0 1471.2017385599474 122.00967689027391 635.7382319173364 0 0 33.63009999999994 -84.44179999999993 307.7999999999999 53.19616204690831 7690.433327866163 13063.511399048712 71.04100377234705 -4.844349680170576 10195.064785960309 35.41438640642938 -87.13800780547811 164.81139904871245 42.93505002460226 10934.489092996555 14502.439232409382 54.1128423814991 -18.662456946039036 10208.477611940298 2 ATL 2.0 1447.5805008944544 120.48479427549195 624.8980322003578 0 0 33.630099999999985 -84.44179999999997 307.8000000000002 40.69081693500298 9296.463923673226 13439.623285629099 58.764609421586165 -13.743738819320214 10191.86747167561 35.40789555008945 -86.77883898777579 160.53200655933216 36.67188431723316 11773.802325581395 14928.161001788909 47.57155635062612 -20.839296362552176 10202.486881335719 6 SUX 6.0 645.0 107.0 436.0 0 0 42.3913 -96.3791 333.8 33.857142857142854 18944.285714285714 14483.714285714286 -57.857142857142854 -81.71428571428571 10170.714285714286 41.995 -87.93359999999998 201.79999999999998 35.285714285714285 8937.42857142857 15633.285714285714 -80.0 -111.14285714285714 10199.57142857143 6 GRK 6.0 1195.3650793650793 59.333333333333336 213.4126984126984 0 0 31.06667 -97.83333000000003 309.4 45.42857142857143 17000.904761904763 15147.904761904761 123.33333333333333 49.46031746031746 10186.777777777777 32.51602380952381 -95.35812698412697 163.44126984126981 45.01587301587302 15404.111111111111 15313.936507936507 104.39682539682539 25.238095238095237 10181.873015873016 6 AUS 6.0 1197.9448946515397 142.93679092382496 860.0956239870341 0 0 30.18310000000001 -97.67990000000002 146.3 34.705024311183145 8118.369529983793 14093.18152350081 101.59643435980551 55.33711507293355 10205.084278768234 35.11746212317665 -98.04130272285252 242.38492706645056 37.32414910858995 12810.62074554295 14666.977309562399 80.6645056726094 3.6012965964343597 10197.502431118315 1 OMA 1.0 1185.1898016997168 120.14164305949008 630.4730878186969 0 0 41.31019999999999 -95.89909999999999 299.3 35.61756373937677 12414.226628895183 15119.677053824362 -54.9971671388102 -108.07648725212465 10264.031161473087 38.499416090651565 -95.712248611898 429.50311614730873 41.623229461756374 11496.388101983002 14920.246458923513 6.113314447592068 -65.02832861189802 10229.699716713882 3 SFO 3.0 1352.0841895923102 166.8213457076566 1115.0662910175672 0 0 37.61970000000002 -122.36470000000011 2.4000000000000035 14.75372886973815 15444.920119323831 14868.644017235665 129.7951607557176 98.8975803778588 10215.709313887968 36.9845013622804 -106.14352879350349 249.48597944978465 31.268147166059 13858.358965860127 14556.539608882997 90.4487901889294 2.032151143520053 10205.89758037786 5 BMI 5.0 1208.057142857143 98.81428571428572 464.07142857142856 0 0 40.48333000000002 -88.94999999999999 263.70000000000005 51.25714285714286 15657.314285714287 14909.057142857142 -51.714285714285715 -97.14285714285714 10265.842857142858 36.557829999999996 -88.47401714285716 206.7614285714285 44.07142857142857 10832.6 15518.271428571428 14.485714285714286 -60.371428571428574 10240.671428571428 1 TUS 1.0 1187.9972899728998 122.40921409214093 708.8373983739838 0 0 32.13129999999999 -110.9552 776.9 33.482384823848236 18680.18699186992 16058.111111111111 153.9159891598916 29.99728997289973 10178.287262872629 36.27638720867209 -107.63697441734419 452.2672086720867 35.45528455284553 12207.246612466124 14226.425474254742 84.23577235772358 4.56639566395664 10213.355013550135 5 SHV 5.0 1109.157894736842 78.74342105263158 342.51973684210526 0 0 32.44719999999999 -93.82440000000001 77.39999999999998 31.44078947368421 

MO O avg_DAY_OF_WEEK avg_CRS_DEP_TIME avg_CRS_ELAPSED_TIME avg_DISTANCE min_FIRST_DEP min_PREVIOUS_DELAY avg_LATITUDE avg_LONGITUDE avg_ELEVATION avg_WND_SPEED avg_CIG_HEIGHT avg_VIS_DIST avg_TEMP avg_DEW_TEMP avg_SLPRESS avg_DEST_LATITUDE avg_DEST_LONGITUDE avg_DEST_ELEVATION avg_DEST_WND_SPEED avg_DEST_CIG_HEIGHT avg_DEST_VIS_DIST avg_DEST_TEMP avg_DEST_DEW_TEMP avg_DEST_SLPRESS 1 MSY 3.98654503990878 1298.860433295325 129.05290763968074 745.923717217788 0 0 29.996909999999986 -90.27750999999995 1.2000000000000013 44.17172177879134 11512.931014823262 15096.64629418472 132.51949828962373 63.308095781071835 10214.779361459521 34.60073413683011 -91.84291559179016 200.87535917901945 40.15199543899658 11457.391220068415 14851.349828962371 80.99327251995439 4.126111744583809 10199.431128848346 7 BWI 4.045754978465737 1379.3843332906913 140.7819282759797 813.3222463860816 0 0 39.17330000000019 -76.68399999999981 47.5 25.67067502451921 12324.196580103195 15022.11223401987 264.3030574389152 192.9322843375549 10142.516140036672 36.671049521555595 -86.6265305419811 202.7119142040853 33.04656517845721 14242.535968615412 15685.841243443776 263.5995053515841 181.77489232868535 10149.719713445056 10 PDX 3.983142592019796 1277.3519950510363 156.97703371481597 1025.710794927312 0 0 45.59580000000004 -122.6093000000001 5.799999999999988 30.411073306526447 8806.902567274978 14975.722007423446 133.2772966285184 90.9358954531395 10164.272424992267 37.76511519486547 -111.31201466826484 311.5719146303743 34.42684812867306 14754.06433652954 15540.760439220538 182.6272811630065 80.94007114135478 10153.140040210332 3 GSP 3.803523035230352 1184.2425474254742 95.6321138211382 403.38482384823845 0 0 34.88419999999998 -82.22090000000013 287.4000000000001 31.107046070460704 14747.586720867208 15198.974932249323 130.12262872628727 41.05555555555556 10192.958672086721 36.52376013550134 -84.46731180216804 198.7671409214092 42.079268292682926 10535.976964769648 14649.865176151761 108.91260162601625 31.074525745257453 10191.812330623306 6 GPT 3.8935574229691876 1153.7156862745098 89.45518207282913 389.10364145658264 0 0 30.411900000000003 -89.08079999999995 12.800000000000004 26.471988795518207 17366.918767507002 15643.91456582633 271.7072829131653 221.35574229691878 10157.43137254902 32.16553277310925 -90.81557661064427 180.3603641456583 31.147058823529413 14015.577030812325 15754.932773109243 270.7829131652661 202.44117647058823 10152.280112044818 7 ACV 4.16 1163.4363636363637 71.13090909090909 250.0 0 0 40.97806 -124.10860999999997 61.0 22.26909090909091 8579.614545454546 13355.770909090908 142.45454545454547 120.71272727272728 10168.407272727272 37.61970000000002 -122.3646999999999 2.3999999999999995 53.57818181818182 16060.476363636364 16069.596363636363 170.54181818181817 117.00727272727272 10144.607272727273 7 LEX 4.000814332247557 1247.055374592834 99.94381107491857 408.42752442996743 0 0 38.04080000000004 -84.60580000000002 298.70000000000005 28.36156351791531 16310.812703583062 14863.146579804561 252.38029315960912 195.14983713355048 10160.287459283387 37.40070008143322 -86.43003607491858 218.88306188925083 33.41123778501629 14207.57654723127 15719.528501628665 263.33469055374593 189.178338762215 10155.795602605864 10 MRY 3.91864406779661 1209.5830508474576 79.52033898305085 289.2406779661017 0 0 36.58805999999999 -121.84528000000002 50.300000000000004 23.279661016949152 16797.898305084746 15194.964406779662 162.9949152542373 99.69322033898305 10167.77627118644 34.706968983050864 -118.0227677966102 86.27084745762713 31.005084745762712 17106.584745762713 15591.157627118644 218.49322033898306 110.28474576271186 10131.035593220338 4 RST 4.116591928251121 1254.3878923766815 78.65022421524664 285.67488789237666 0 0 43.904099999999985 -92.4916 397.5 60.33408071748879 13319.235426008969 15254.997757847534 95.76233183856502 18.91255605381166 10154.822869955156 41.746129147982074 -89.4160786995516 243.9748878923766 50.34304932735426 11165.251121076233 15595.0

# F) Create helper table for imputing validation data (when ORIGIN not in training data)
(Averages of training data features)

In [0]:
#Since there are many null average data (because of airports in validation/test data that are missing from training data), impute these nulls with the average of all airports

#Create average lookup table
avg_lookup = train_dropqual_dropna_drop99999.select( avg_('DAY_OF_WEEK').alias('avg_DAY_OF_WEEKa'),
                                  avg_('CRS_DEP_TIME').alias('avg_CRS_DEP_TIMEa'),
                                  avg_('CRS_ELAPSED_TIME').alias('avg_CRS_ELAPSED_TIMEa'),
                                  avg_('DISTANCE').alias('avg_DISTANCEa'),
                                  min_('FIRST_DEP').alias('min_FIRST_DEPa'),
                                  min_('PREVIOUS_DELAY').alias('min_PREVIOUS_DELAYa'),
                                  avg_('LATITUDE').alias('avg_LATITUDEa'),
                                  avg_('LONGITUDE').alias('avg_LONGITUDEa'),
                                  avg_('ELEVATION').alias('avg_ELEVATIONa'),
                                  avg_('WND_SPEED').alias('avg_WND_SPEEDa'),
                                  avg_('CIG_HEIGHT').alias('avg_CIG_HEIGHTa'),
                                  avg_('VIS_DIST').alias('avg_VIS_DISTa'),
                                  avg_('TEMP').alias('avg_TEMPa'),
                                  avg_('DEW_TEMP').alias('avg_DEW_TEMPa'),
                                  avg_('SLPRESS').alias('avg_SLPRESSa'),
                                             
                                  avg_('DEST_LATITUDE').alias('avg_DEST_LATITUDEa'),
                                  avg_('DEST_LONGITUDE').alias('avg_DEST_LONGITUDEa'),
                                  avg_('DEST_ELEVATION').alias('avg_DEST_ELEVATIONa'),
                                  avg_('DEST_WND_SPEED').alias('avg_DEST_WND_SPEEDa'),
                                  avg_('DEST_CIG_HEIGHT').alias('avg_DEST_CIG_HEIGHTa'),
                                  avg_('DEST_VIS_DIST').alias('avg_DEST_VIS_DISTa'),
                                  avg_('DEST_TEMP').alias('avg_DEST_TEMPa'),
                                  avg_('DEST_DEW_TEMP').alias('avg_DEST_DEW_TEMPa'),
                                  avg_('DEST_SLPRESS').alias('avg_DEST_SLPRESSa')    )
#Store Data         
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/avg_lookup", True)      #remove file if there already is an existing one, be careful with this!!!
avg_lookup.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/avg_lookup")  

In [0]:
# Read in Avg Lookup Table
avg_lookup = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/avg_lookup/part-00*.parquet")
avg_lookup.display()

avg_DAY_OF_WEEKa avg_CRS_DEP_TIMEa avg_CRS_ELAPSED_TIMEa avg_DISTANCEa min_FIRST_DEPa min_PREVIOUS_DELAYa avg_LATITUDEa avg_LONGITUDEa avg_ELEVATIONa avg_WND_SPEEDa avg_CIG_HEIGHTa avg_VIS_DISTa avg_TEMPa avg_DEW_TEMPa avg_SLPRESSa avg_DEST_LATITUDEa avg_DEST_LONGITUDEa avg_DEST_ELEVATIONa avg_DEST_WND_SPEEDa avg_DEST_CIG_HEIGHTa avg_DEST_VIS_DISTa avg_DEST_TEMPa avg_DEST_DEW_TEMPa avg_DEST_SLPRESSa 3.942869869943395 1336.1695987819908 145.05387984885908 846.0186153945617 0 0 36.66500090109792 -96.0239866126912 253.3793025421035 38.581142655405 13082.74633962568 15341.070194213306 173.06952671824973 84.81701658819989 10165.1129698825 36.66381468722042 -96.05805652637845 253.06262291705212 38.49919856590109 13135.569034051387 15351.528574847283 173.61805946460262 85.14554648449783 10165.283138336996

# Rename Data Files for Modeling

In [0]:
#Split Data to 3month baseline, 3 month, and full train
train_data_3m_baseline = train_data_3m_dw_b.where("ORIGIN = 'ATL' or ORIGIN = 'ORD'")
train_data_3m = train_data_3m_dw_b
train_data = train_data_dw_b

#SAVING Spark Dataframe to Shared Directory
file_to_store = train_data_3m_baseline                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data_3m_baseline"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

file_to_store = train_data_3m                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data_3m"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

file_to_store = train_data                        #CHANGE THIS: name of Spark Dataframe (to save in database)
filename = "train_data"                      #CHANGE THIS: new file name in database
dbutils.fs.rm("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename, True)      #remove file if there already is an existing one, be careful with this!!!
file_to_store.write.parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/" + filename)

In [0]:
#Read 3month baseline, 3 month, and full train data

#Read Data
filename = "train_data_3m_baseline"                      
train_data_3m_baseline = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
train_data_3m_baseline.display()
print("train_data_3m_baseline Shape:", train_data_3m_baseline.count(), len(train_data_3m_baseline.columns))

############################################

filename = "train_data_3m"                      
train_data_3m = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
train_data_3m.display()
print("train_data_3m:", train_data_3m.count(), len(train_data_3m.columns))

############################################

filename = "train_data"                      
train_data = spark.read.option("header", "true").parquet("dbfs:/mnt/mids-w261/team_25/train_test_data_folder/"+filename+"/part-00*.parquet")
train_data.display()
print("train_data:", train_data.count(), len(train_data.columns))

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2015 1 4 AA ATL GA DFW TX 3.0 150.0 731.0 0 0 13951 33.6301 -84.4418 307.8 0.0 1.0 1.0 N 17 -33 10274 0.06178103047926055 32.8978 -97.0189 170.7 N 0 -39 10282 2.0 1.0 0.0 1 2015 1 4 DL ATL GA CVG KY 6.0 86.0 373.0 0 0 13951 33.6301 -84.4418 307.8 0.0 0.0 1.0 N 61 -28 10280 0.06178103047926055 39.0444 -84.6724 269.1 N -33 -117 10245 2.0 1.0 1.0 0 2015 1 4 DL ATL GA SAT TX 5.0 171.0 874.0 0 0 13951 33.6301 -84.4418 307.8 0.0 1.0 1.0 N 28 -22 10276 0.06178103047926055 29.5443 -98.4839 240.5 N 28 22 10242 1.0 0.0 0.0 0 2015 1 4 EV ATL GA BTR LA 7.0 98.0 448.0 0 0 13951 33.6301 -84.4418 307.8 1.0 0.0 1.0 N 100 -61 10270 0.06178103047926055 30.5372 -91.1469 19.5 N 83 44 10252 2.0 1.0 0.0 0 2015 1 5 MQ ORD IL CID IA 4.0 63.0 196.0 0 0 16721 41.995 -87.9336 201.8 0.0 1.0 1.0 N -72 -94 10243 0.04737763713846122 41.8833 -91.7166 264.6 N -89 -106 10238 1.0 1.0 1.0 1 2015 1 5 MQ ORD IL CLE OH 3.0 73.0 315.0 0 0 16721 41.995 -87.9336 201.8 1.0 1.0 1.0 N -72 -94 10232 0.04737763713846122 41.4057 -81.852 238.0 N -28 -89 10238 2.0 1.0 0.0 1 2015 1 5 MQ ORD IL PIT PA 6.0 83.0 413.0 0 0 16721 41.995 -87.9336 201.8 0.0 1.0 1.0 N -28 -72 10272 0.04737763713846122 40.4846 -80.2144 366.7 N -6 -78 10278 2.0 1.0 1.0 0 2015 1 5 UA ORD IL IAH TX 7.0 177.0 925.0 0 0 16721 41.995 -87.9336 201.8 1.0 0.0 1.0 N 6 -78 10251 0.04737763713846122 29.98 -95.36 29.0 N 111 106 10175 0.0 0.0 0.0 1 2015 1 6 DL ATL GA LAX CA 9.0 310.0 1947.0 0 0 15409 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 122 117 10206 0.06178103047926055 33.938 -118.3888 29.6 N 144 72 10229 2.0 1.0 1.0 1 2015 1 6 DL ATL GA MSY LA 11.0 96.0 425.0 0 1 15409 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 128 122 10199 0.06178103047926055 29.99691 -90.27751 1.2 N 228 206 10160 2.0 1.0 0.0 1 2015 1 6 EV ATL GA CHA TN 8.0 46.0 106.0 0 0 15409 33.6301 -84.4418 307.8 2.0 0.0 0.0 N 117 111 10213 0.06178103047926055 35.03362 -85.20044 204.2 N 122 117 10188 1.0 0.0 0.0 1 2015 1 6 EV ATL GA OMA NE 4.0 149.0 821.0 0 0 15409 33.6301 -84.4418 307.8 2.0 0.0 0.0 N 94 83 10237 0.06178103047926055 41.3102 -95.8991 299.3 N -44 -56 10129 1.0 0.0 0.0 1 2015 1 6 OO ORD IL AVL NC 6.0 104.0 536.0 0 0 15409 41.995 -87.9336 201.8 0.0 0.0 0.0 N 6 0 10132 0.04737763713846122 35.4319 -82.5375 645.3 N 78 67 10252 2.0 0.0 0.0 1 2015 1 6 UA ORD IL CLE OH 9.0 86.0 315.0 0 0 15409 41.995 -87.9336 201.8 1.0 0.0 0.0 N 11 0 10090 0.04737763713846122 41.4057 -81.852 238.0 N 94 78 10116 2.0 0.0 0.0 1 2015 1 6 US ATL GA CLT NC 6.0 69.0 226.0 0 0 15409 33.6301 -84.4418 307.8 2.0 0.0 0.0 N 111 100 10233 0.06178103047926055 35.2236 -80.9552 221.9 N 100 78 10264 1.0 0.0 0.0 0 2015 1 7 EV ATL GA TUL OK 7.0 132.0 674.0 0 0 16330 33.6301 -84.4418 307.8 2.0 0.0 1.0 N 167 139 10176 0.06178103047926055 36.1994 -95.8872 198.1 N -39 -117 10362 2.0 1.0 1.0 1 2015 1 7 MQ ORD IL CMI IL 9.0 48.0 135.0 0 0 16330 41.995 -87.9336 201.8 2.0 1.0 1.0 N -100 -139 10251 0.04737763713846122 40.03972 -88.27778 229.8 N -83 -117 10278 2.0 0.0 0.0 1 2015 1 7 OO ORD IL MSP MN 3.0 95.0 334.0 0 0 16330 41.995 -87.9336 201.8 2.0 0.0 0.0 N 0 -6 10069 0.04737763713846122 44.8831 -93.2289 265.8 N -167 -233 10252 2.0 1.0 0.0 0 2015 1 1 AA ORD IL BOS MA 6.0 135.0 867.0 0 0 16523 41.995 -87.9336 201.8 2.0 0.0 1.0 N -178 -222 10379 0.04737763713846122 42.3606 -71.0097 3.7 N 11 -139 10138 3.0 1.0 1.0 0 2015 1 1 EV ATL GA CAE SC 8.0 55.0 192.0 0 0 16523 33.6301 -84.4418 307.8 2.0 1.0 1.0 N 78 -50 10322 0.06178103047926055 33.9419 -81.1181 68.6 N 128 -28 10292 2.0 1.0 1.0 0 2015 1 1 EV ORD IL SYR NY 7.0 107.0 607.0 0 0 16523 41.995 -87.9336 201.8 2.0 0.0 1.0

train_data_3m_baseline Shape: 84422 36

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2015 1 4 AA BOS MA ORD IL 8.0 185.0 867.0 0 0 13951 42.3606 -71.0097 3.7 2.0 0.0 1.0 N -6 -139 10135 0.016488988638580226 41.995 -87.9336 201.8 N -6 -100 10155 2.0 1.0 0.0 0 2015 1 4 AA ORD IL DCA VA 11.0 100.0 612.0 0 0 13951 41.995 -87.9336 201.8 2.0 0.0 1.0 N -22 -94 10198 0.04737763713846122 38.8472 -77.03454 3.0 N 33 -61 10185 2.0 1.0 1.0 0 2015 1 4 AA TPA FL DFW TX 4.0 170.0 929.0 0 0 13951 27.96194 -82.5403 5.8 2.0 0.0 1.0 N 150 122 10237 0.009735873905956583 32.8978 -97.0189 170.7 N 6 -28 10273 2.0 1.0 0.0 0 2015 1 4 AS DCA VA PDX OR 8.0 356.0 2350.0 0 0 13951 38.8472 -77.03454 3.0 2.0 0.0 1.0 N 72 -94 10191 0.010509557105859428 45.5958 -122.6093 5.8 N 17 -89 10263 1.0 1.0 1.0 0 2015 1 4 AS SEA WA ANC AK 3.0 234.0 1448.0 0 0 13951 47.4444 -122.3138 112.8 1.0 1.0 1.0 N -11 -61 10291 0.022200771421814543 61.169 -150.0278 36.6 N 11 0 10201 0.0 0.0 0.0 0 2015 1 4 AS SJC CA SEA WA 3.0 124.0 697.0 0 0 13951 37.3591 -121.924 15.5 1.0 1.0 1.0 N 22 -61 10187 0.006585447900909955 47.4444 -122.3138 112.8 N -11 -61 10291 1.0 1.0 1.0 0 2015 1 4 B6 LAS NV LGB CA 5.0 64.0 231.0 0 0 13951 36.0719 -115.1634 664.5 2.0 1.0 1.0 N 17 -72 10204 0.02129887021282643 33.8116 -118.1463 9.4 N 72 -22 10214 1.0 1.0 1.0 0 2015 1 4 DL ATL GA DCA VA 9.0 104.0 547.0 0 0 13951 33.6301 -84.4418 307.8 1.0 0.0 1.0 N 122 -11 10253 0.06178103047926055 38.8472 -77.03454 3.0 N 61 -89 10188 2.0 1.0 0.0 0 2015 1 4 DL ATL GA DTW MI 10.0 114.0 594.0 0 0 13951 33.6301 -84.4418 307.8 0.0 0.0 1.0 N 111 -11 10258 0.06178103047926055 42.2313 -83.3308 192.3 N -17 -106 10161 2.0 1.0 0.0 0 2015 1 4 DL ATL GA FLL FL 5.0 115.0 581.0 0 0 13951 33.6301 -84.4418 307.8 0.0 1.0 1.0 N 28 -22 10276 0.06178103047926055 26.07875 -80.16217 3.4 N 233 217 10225 1.0 1.0 0.0 0 2015 1 4 DL ATL GA ORD IL 5.0 130.0 606.0 0 0 13951 33.6301 -84.4418 307.8 0.0 1.0 1.0 N 28 -22 10276 0.06178103047926055 41.995 -87.9336 201.8 N -94 -144 10186 2.0 1.0 1.0 0 2015 1 4 DL ATL GA SDF KY 10.0 81.0 321.0 0 0 13951 33.6301 -84.4418 307.8 1.0 0.0 1.0 N 117 -11 10254 0.06178103047926055 38.1811 -85.7391 148.7 N 33 -56 10234 1.0 1.0 0.0 0 2015 1 4 DL MSP MN MIA FL 3.0 226.0 1501.0 0 0 13951 44.8831 -93.2289 265.8 2.0 0.0 1.0 N -94 -133 10130 0.0228724306628863 25.7881 -80.3169 8.8 N 217 200 10211 1.0 0.0 0.0 0 2015 1 4 EV ATL GA AZO MI 9.0 115.0 596.0 0 0 13951 33.6301 -84.4418 307.8 1.0 0.0 1.0 N 122 -11 10253 0.06178103047926055 42.23472 -85.55194 264.6 N -22 -89 10156 2.0 1.0 0.0 0 2015 1 4 EV EWR NJ CLE OH 8.0 100.0 404.0 0 0 13951 40.6825 -74.1694 2.1 2.0 1.0 1.0 N 33 -133 10166 0.016227158507187554 41.4057 -81.852 238.0 N 0 -128 10162 3.0 1.0 1.0 0 2015 1 4 EV IAD VA PVD RI 8.0 81.0 372.0 0 0 13951 38.93486 -77.44728 88.4 2.0 0.0 1.0 N 44 -89 10186 0.0054061753716854255 41.7225 -71.4325 16.8 N 6 -128 10144 2.0 1.0 0.0 0 2015 1 4 EV IAH TX MAF TX 8.0 91.0 429.0 0 0 13951 29.98 -95.36 29.0 2.0 0.0 0.0 N 67 56 10208 0.02232401241556353 31.9475 -102.2086 872.3 N -39 -50 10208 1.0 0.0 0.0 1 2015 1 4 EV MOB AL IAH TX 4.0 94.0 427.0 0 0 13951 30.68833 -88.24556 65.5 1.0 0.0 0.0 N 50 44 10265 0.001131451668123938 29.98 -95.36 29.0 N 56 28 10251 2.0 1.0 0.0 0 2015 1 4 EV ORD IL ERI PA 6.0 88.0 398.0 0 0 13951 41.995 -87.9336 201.8 2.0 1.0 1.0 N -50 -128 10174 0.04737763713846122 42.0803 -80.1824 222.2 N -22 -139 10152 2.0 1.0 1.0 0 2015 1 4 EV SAV GA LGA NY 7.0 130.0 722.0 0 1 13951 32.13133 -81.20237 14.0 1.0 0.0 1.0 N 144 17 10261 0.001529360239480589 40.7792 -73.88 3.4 N 22 -133 10176 2.0 1.0 1.0 0 2015 1 4 HA LIH HI HNL HI 4.0 32.0 102.0 0 0 13951 21.98389 -159.34056 30

train_data_3m: 753364 36

YEAR MONTH DAY_OF_WEEK OP_UNIQUE_CARRIER ORIGIN ORIGIN_STATE_ABR DEST DEST_STATE_ABR CRS_DEP_TIME_BUCK CRS_ELAPSED_TIME DISTANCE FIRST_DEP PREVIOUS_DELAY FLIGHTS_PER_DAY LATITUDE LONGITUDE ELEVATION WND_SPEED_BUCK CIG_HEIGHT_BUCK VIS_DIST_BUCK VIS_VAR TEMP DEW_TEMP SLPRESS PAGERANK DEST_LATITUDE DEST_LONGITUDE DEST_ELEVATION DEST_VIS_VAR DEST_TEMP DEST_DEW_TEMP DEST_SLPRESS DEST_WND_SPEED_BUCK DEST_VIS_DIST_BUCK DEST_CIG_HEIGHT_BUCK DELAY 2015 12 4 AA DEN CO DFW TX 3.0 128.0 641.0 0 1 16217 39.8328 -104.6575 1650.2 2.0 1.0 1.0 N 94 -89 10060 0.03621702748797421 32.8978 -97.0189 170.7 N 122 67 10076 2.0 1.0 0.0 0 2015 12 4 AA DFW TX SEA WA 5.0 266.0 1660.0 0 0 16217 32.8978 -97.0189 170.7 2.0 0.0 1.0 N 122 94 10078 0.03817073608327177 47.4444 -122.3138 112.8 N 94 56 9901 2.0 1.0 0.0 0 2015 12 4 AA IND IN PHX AZ 9.0 239.0 1488.0 0 1 16217 39.72517 -86.28168 241.1 2.0 0.0 1.0 N 133 67 10054 0.004076538833610215 33.4277 -112.0038 337.4 N 233 -6 10114 1.0 1.0 0.0 0 2015 12 4 AA ORD IL AUS TX 9.0 178.0 977.0 0 0 16217 41.995 -87.9336 201.8 3.0 0.0 1.0 N 128 56 9981 0.04737763713846122 30.1831 -97.6799 146.3 N 256 139 10075 2.0 1.0 0.0 0 2015 12 4 AA SEA WA DFW TX 6.0 230.0 1660.0 0 0 16217 47.4444 -122.3138 112.8 2.0 0.0 0.0 N 83 56 9900 0.022200771421814543 32.8978 -97.0189 170.7 N 217 100 10070 2.0 1.0 0.0 0 2015 12 4 AA SFO CA PHL PA 5.0 320.0 2521.0 0 1 16217 37.6197 -122.3647 2.4 2.0 0.0 1.0 N 139 94 10126 0.026173769929446686 39.87327 -75.22678 3.0 N 122 67 10164 0.0 0.0 1.0 0 2015 12 4 AS PDX OR LAX CA 4.0 140.0 834.0 0 0 16217 45.5958 -122.6093 5.8 2.0 0.0 0.0 N 94 94 9925 0.00860241859146984 33.938 -118.3888 29.6 V 144 133 10157 1.0 0.0 0.0 0 2015 12 4 B6 PBI FL BOS MA 5.0 175.0 1197.0 0 0 16217 26.6847 -80.0994 5.8 1.0 0.0 0.0 N 211 206 10167 0.0037684605603798315 42.3606 -71.0097 3.7 N 94 72 10161 1.0 1.0 0.0 0 2015 12 4 B6 ROC NY JFK NY 4.0 74.0 264.0 0 0 16217 43.1167 -77.6767 164.3 0.0 0.0 0.0 N 44 33 10132 0.0014879879200592801 40.6386 -73.7622 3.4 N 106 78 10151 2.0 1.0 0.0 0 2015 12 4 DL ATL GA HNL HI 5.0 616.0 4502.0 0 1 16217 33.6301 -84.4418 307.8 1.0 1.0 1.0 N 106 94 10170 0.06178103047926055 21.324 -157.9294 2.1 N 250 178 10184 2.0 1.0 1.0 0 2015 12 4 DL ATL GA MDW IL 6.0 120.0 591.0 0 0 16217 33.6301 -84.4418 307.8 1.0 0.0 0.0 N 144 122 10179 0.06178103047926055 41.78611 -87.75222 186.5 N 111 33 10009 2.0 1.0 0.0 1 2015 12 4 DL ATL GA PIT PA 7.0 100.0 526.0 0 0 16217 33.6301 -84.4418 307.8 2.0 0.0 1.0 N 156 122 10173 0.06178103047926055 40.4846 -80.2144 366.7 N 100 61 10149 2.0 0.0 0.0 0 2015 12 4 DL BOS MA MCO FL 3.0 211.0 1121.0 0 0 16217 42.3606 -71.0097 3.7 1.0 0.0 1.0 N 72 50 10162 0.016488988638580226 28.4339 -81.325 27.4 N 167 144 10152 1.0 1.0 0.0 0 2015 12 4 DL BWI MD ATL GA 4.0 125.0 577.0 0 0 16217 39.1733 -76.684 47.5 0.0 1.0 0.0 N 22 22 10157 0.013487763867768883 33.6301 -84.4418 307.8 N 111 89 10162 1.0 1.0 1.0 0 2015 12 4 DL DEN CO ATL GA 6.0 166.0 1199.0 0 0 16217 39.8328 -104.6575 1650.2 2.0 0.0 1.0 N 117 -78 10042 0.03621702748797421 33.6301 -84.4418 307.8 N 161 122 10163 2.0 1.0 0.0 0 2015 12 4 DL JFK NY BOS MA 10.0 77.0 187.0 0 0 16217 40.6386 -73.7622 3.4 2.0 0.0 0.0 N 117 89 10153 0.014589032926165355 42.3606 -71.0097 3.7 N 94 83 10154 1.0 1.0 0.0 0 2015 12 4 DL LAS NV DTW MI 3.0 233.0 1749.0 0 0 16217 36.0719 -115.1634 664.5 1.0 0.0 1.0 N 72 -22 10120 0.02129887021282643 42.2313 -83.3308 192.3 N 33 28 10104 1.0 0.0 0.0 0 2015 12 4 DL MSP MN DCA VA 3.0 153.0 931.0 0 0 16217 44.8831 -93.2289 265.8 1.0 0.0 1.0 N 56 33 9929 0.0228724306628863 38.8472 -77.03454 3.0 N 56 44 10158 1.0 0.0 1.0 0 2015 12 4 DL MSP MN STL MO 3.0 98.0 448.0 0 0 16217 44.8831 -93.2289 265.8 1.0 0.0 1.0 N 56 33 9929 0.0228724306628863 38.7525 -90.3736 161.8 N 100 28 10079 1.0 1.0 0.0 0 2015 12 4 DL ORD IL ATL GA 8.0 121.0 606.0 0 0 16217 41.995 -87.9336 201.8 2.0 0.0 1.0 N 139 44 9971 0.04737763713846122 33.6301 -84.4418 307.8 N 183 122 10148 1.0 1.0 1.0 0 2015 12 4 DL SJU PR JFK NY 8.0 255.0 1598.0 0 0 16217 18.4325 

train_data: 14771645 36